In [2]:
import numpy as np
import matplotlib.pyplot as plt
from matplotlib.animation import FuncAnimation
from IPython.display import HTML # Essential for displaying in Jupyter

# --- Parameters ---
L = 10.0          # Length of the domain
Nx = 200          # Number of spatial points
dx = L / Nx       # Spatial step size
T_final = 2.0     # Final simulation time
CFL = 0.8         # CFL number
u_L_initial = 2.0 # Left state for initial condition
u_R_initial = 1.0 # Right state for initial condition
x_shock_initial = L / 2 # Initial shock position

# --- Grid Initialization ---
x = np.linspace(0, L, Nx + 1) # Nx+1 points for Nx cells

# --- Initial Condition (Step Function) ---
def initial_condition(x_coords, u_L, u_R, x_shock_pos):
    u = np.zeros_like(x_coords)
    u[x_coords <= x_shock_pos] = u_L
    u[x_coords > x_shock_pos] = u_R
    return u

u_initial = initial_condition(x, u_L_initial, u_R_initial, x_shock_initial)

# --- Analytical Solution ---
def analytical_solution(x_coords, t, u_L, u_R, x_shock_initial_pos):
    s = (u_L + u_R) / 2.0  # Shock speed
    x_shock_t = x_shock_initial_pos + s * t
    u_analytical = np.zeros_like(x_coords)
    u_analytical[x_coords <= x_shock_t] = u_L
    u_analytical[x_coords > x_shock_t] = u_R
    return u_analytical

# --- Calculate dt based on CFL ---
max_u = max(abs(u_L_initial), abs(u_R_initial))
dt = CFL * dx / max_u
Nt = int(T_final / dt) + 1 # Number of time steps

print(f"Simulation Parameters:")
print(f"  dx: {dx:.4f}")
print(f"  dt: {dt:.4f}")
print(f"  Number of time steps: {Nt}")
print(f"  Final Time: {Nt * dt:.4f}")

# --- Flux Function for Burgers' Equation ---
def F(u_val):
    return 0.5 * u_val**2

# --- FDM Schemes ---
def solve_fdm_lax_friedrichs(u_init, delta_t, delta_x, num_time_steps):
    u = np.copy(u_init)
    u_history = [u_init.copy()]
    for n in range(num_time_steps):
        u_new = np.zeros_like(u)
        # Apply boundary conditions (simple constant extrapolation)
        u_new[0] = u[0]
        u_new[-1] = u[-1]

        for i in range(1, len(u) - 1):
            u_new[i] = 0.5 * (u[i+1] + u[i-1]) - (delta_t / (2 * delta_x)) * (F(u[i+1]) - F(u[i-1]))
        u = u_new.copy()
        u_history.append(u.copy())
    return u_history

def solve_fdm_upwind(u_init, delta_t, delta_x, num_time_steps):
    u = np.copy(u_init)
    u_history = [u_init.copy()]
    for n in range(num_time_steps):
        u_new = np.zeros_like(u)
        # Apply boundary conditions
        u_new[0] = u[0]
        u_new[-1] = u[-1]

        for i in range(1, len(u) - 1):
            if u[i] >= 0: # Upwind from left (backward difference)
                u_new[i] = u[i] - (delta_t / delta_x) * u[i] * (u[i] - u[i-1])
            else: # Upwind from right (forward difference)
                u_new[i] = u[i] - (delta_t / delta_x) * u[i] * (u[i+1] - u[i])
        u = u_new.copy()
        u_history.append(u.copy())
    return u_history

# --- Run Simulations ---
print("Calculating analytical solution...")
u_history_analytical = [analytical_solution(x, n * dt, u_L_initial, u_R_initial, x_shock_initial) for n in range(Nt + 1)]

print("Running FDM (Lax-Friedrichs) simulation...")
u_history_fdm_lax_friedrichs = solve_fdm_lax_friedrichs(u_initial, dt, dx, Nt)

print("Running FDM (Upwind) simulation...")
u_history_fdm_upwind = solve_fdm_upwind(u_initial, dt, dx, Nt)


# --- Animation ---
print("Creating animation...")
fig, ax = plt.subplots(figsize=(10, 6))
line_analytical, = ax.plot(x, u_history_analytical[0], 'k--', label='Analytical', linewidth=2)
line_fdm_lf, = ax.plot(x, u_history_fdm_lax_friedrichs[0], 'r-.', label='FDM (Lax-Friedrichs)', linewidth=1.5)
line_fdm_upwind, = ax.plot(x, u_history_fdm_upwind[0], 'g:', label='FDM (Upwind)', linewidth=1.5)

ax.set_title("1D Burgers' Equation with Shock (Time: 0.00)", fontsize=14)
ax.set_xlabel("x", fontsize=12)
ax.set_ylabel("u", fontsize=12)
ax.legend(loc='upper right', fontsize=10)
ax.set_ylim(min(u_R_initial, u_L_initial) - 0.2, max(u_R_initial, u_L_initial) + 0.2)
ax.grid(True)

def update(frame):
    current_time = frame * dt
    line_analytical.set_ydata(u_history_analytical[frame])
    line_fdm_lf.set_ydata(u_history_fdm_lax_friedrichs[frame])
    line_fdm_upwind.set_ydata(u_history_fdm_upwind[frame])
    ax.set_title(f"1D Burgers' Equation with Shock (Time: {current_time:.2f})")
    # Return all updated lines in the tuple for blitting
    return line_analytical, line_fdm_lf, line_fdm_upwind

# The blit=True optimization doesn't always work perfectly in all Jupyter environments
# If you face issues, try setting blit=False, but it might be slower.
ani = FuncAnimation(fig, update, frames=len(u_history_analytical), blit=True, interval=50) # interval in ms

# To display the animation in Jupyter, save it as HTML5 video
# Requires ffmpeg to be installed on your system
print("Saving animation as HTML5 video for Jupyter display...")
html_video = HTML(ani.to_jshtml())
plt.close(fig) # Close the plot to prevent it from showing twice (once as static, once as video)
print("Animation ready.")
html_video

Simulation Parameters:
  dx: 0.0500
  dt: 0.0200
  Number of time steps: 100
  Final Time: 2.0000
Calculating analytical solution...
Running FDM (Lax-Friedrichs) simulation...
Running FDM (Upwind) simulation...
Creating animation...
Saving animation as HTML5 video for Jupyter display...
Animation ready.
